In [1]:
import pandas as pd 
import numpy as np
import json
#from geopy.geocoders import Nominatim 
import requests 
from pandas.io.json import json_normalize 
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.cm as cm
import folium
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
from folium import plugins
from folium.plugins import HeatMap
import matplotlib.colors as colors
from sklearn.cluster import KMeans

/home/mike/Documents/Projects/Coursera_Capstone/Capstone


In [2]:
arrest_data=pd.read_csv('NYPD_Arrest_Data__Year_to_Date_.csv')

shots_data=pd.read_csv('NYPD_Shooting_Incident_Data__Year_To_Date_.csv')

In [3]:
arrest_data.head()

In [37]:
shots_data.head(50)

INCIDENT_KEY  OCCUR_DATE OCCUR_TIME           BORO  PRECINCT  \
0      199134397  06/30/2019   21:35:00         QUEENS       101   
1      199134405  06/30/2019   04:24:00      MANHATTAN        10   
2      199134404  06/30/2019   03:33:00  STATEN ISLAND       120   
3      199134399  06/30/2019   01:20:00          BRONX        41   
4      199134403  06/29/2019   18:39:00       BROOKLYN        83   
5      199134401  06/29/2019   06:00:00       BROOKLYN        70   
6      199134406  06/29/2019   05:48:00       BROOKLYN        69   
7      199134406  06/29/2019   05:48:00       BROOKLYN        69   
8      199134398  06/28/2019   17:35:00       BROOKLYN        73   
9      199134398  06/28/2019   17:35:00       BROOKLYN        73   
10     199134402  06/28/2019   12:34:00       BROOKLYN        72   
11     199134400  06/28/2019   04:30:00         QUEENS       110   
12     199061351  06/28/2019   00:26:00       BROOKLYN        83   
13     199052835  06/28/2019   00:25:00          BRONX        42   
14     199046249  06/27/2019   21:02:00         QUEENS       101   
15     199046250  06/27/2019   01:00:00          BRONX        52   
16     199046251  06/27/2019   00:15:00          BRONX        46   
17     198998743  06/26/2019   20:45:00       BROOKLYN        81   
18     198998742  06/26/2019   00:36:00         QUEENS       114   
19     198948496  06/25/2019   22:24:00       BROOKLYN        81   
20     198948498  06/25/2019   16:48:00         QUEENS       108   
21     198948497  06/25/2019   02:55:00          BRONX        42   
22     198948495  06/25/2019   01:20:00         QUEENS       109   
23     198948494  06/25/2019   00:01:00          BRONX        48   
24     198900605  06/24/2019   18:55:00      MANHATTAN        32   
25     198900606  06/24/2019   02:49:00          BRONX        41   
26     198900607  06/24/2019   00:05:00       BROOKLYN        60   
27     198858232  06/23/2019   23:08:00          BRONX        43   
28     198858233  06/23/2019   20:35:00          BRONX        50   
29     198858231  06/23/2019   16:00:00          BRONX        44   
30     198858231  06/23/2019   16:00:00          BRONX        44   
31     198858230  06/23/2019   12:02:00       BROOKLYN        61   
32     198858229  06/23/2019   02:15:00          BRONX        46   
33     198858229  06/23/2019   02:15:00          BRONX        46   
34     198858227  06/23/2019   00:30:00      MANHATTAN        30   
35     198857666  06/22/2019   22:30:00          BRONX        44   
36     198857666  06/22/2019   22:30:00          BRONX        44   
37     198858228  06/22/2019   02:36:00       BROOKLYN        94   
38     198857665  06/21/2019   23:30:00          BRONX        40   
39     198760075  06/20/2019   19:09:00       BROOKLYN        75   
40     198760073  06/20/2019   19:02:00       BROOKLYN        77   
41     198760073  06/20/2019   19:02:00       BROOKLYN        77   
42     198760074  06/20/2019   17:43:00       BROOKLYN        63   
43     198705941  06/19/2019   18:01:00       BROOKLYN        73   
44     198705943  06/19/2019   10:40:00      MANHATTAN         5   
45     198653292  06/18/2019   10:50:00       BROOKLYN        73   
46     198595255  06/17/2019   23:21:00       BROOKLYN        73   
47     198595257  06/17/2019   17:34:00          BRONX        43   
48     198595258  06/17/2019   14:47:00       BROOKLYN        81   
49     198552502  06/15/2019   04:14:00      MANHATTAN        32   

    JURISDICTION_CODE              LOCATION_DESC  STATISTICAL_MURDER_FLAG  \
0                 0.0                        NaN                    False   
1                 2.0  MULTI DWELL - PUBLIC HOUS                    False   
2                 0.0                        NaN                    False   
3                 0.0    MULTI DWELL - APT BUILD                     True   
4                 0.0                        NaN                    False   
5                 0.0                        NaN                    False

In [20]:
lat_shots=list(shots_data.Latitude)
lon_shots=list(shots_data.Longitude)


In [9]:
#sorting for only assault, burglary,weapons, sexual abuse, larceny, bringing data size down to ~45k
arrest_data=arrest_data.dropna()

arrest_data=arrest_data[arrest_data["PD_DESC"].str.contains('assault|theft|assault|burglary|weapons|sexual abuse|larceny',case=False)]
arrestloc=arrest_data[['Latitude','Longitude']]
shotsloc=shots_data[['Latitude','Longitude']]
arrestloc.shape

(45881, 2)

In [14]:
heat = arrestloc
data = heat.as_matrix(['Latitude','Longitude']).tolist()

/home/mike/miniconda3/envs/Capstone/lib/python3.7/site-packages/ipykernel_launcher.py:2: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  


In [15]:
arrestloc=arrest_data[['OFNS_DESC','Latitude','Longitude']]
arrestloc.shape

(45881, 3)

In [16]:
#Extract longitude and latidude
import pygeoj
latitude_sub=[]
longitude_sub=[]
names=[]
lines=[]
testfile = pygeoj.load("Subway Entrances.geojson")
for feature in testfile:
    lines.append(feature.properties['line'])
    names.append(feature.properties['name'])
    latitude_sub.append(feature.geometry.coordinates[1])
    longitude_sub.append(feature.geometry.coordinates[0])

In [17]:
latitude=40.7128
longitude=-74.006
map_ny = folium.Map(location=[latitude, longitude], zoom_start=10)
colormap = {0.0: 'pink', 0.3: 'blue', 0.5: 'green',  0.7: 'yellow', 1.0: 'red'}

# plotting coordinates of postal code, with stopname as labels in popup
for lat, lng, name, line in zip(latitude_sub, longitude_sub, names, lines):
    label = 'Stop Name:{} Line:{}'.format(name,line)
    label = folium.Popup(label)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=True).add_to(map_ny)  
    
HeatMap(data, min_opacity=0.5,fill_opacity=.2,
        max_zoom=18, 
        max_val=1.0, 
        radius=15,
        blur=20,
        gradient=colormap,
        use_local_extrema=True,
        overlay=True).add_to(map_ny)
    
map_ny

In [39]:
latitude=40.7128
longitude=-74.006
map_nys = folium.Map(location=[latitude, longitude], zoom_start=10)
colormap = {0.0: 'pink', 0.3: 'blue', 0.5: 'green',  0.7: 'yellow', 1.0: 'red'}

# plotting coordinates of postal code, with stopname as labels in popup
for  latshot, lonshot, boro in zip(lat_shots, lon_shots,list(shots_data.BORO) ):
    folium.Circle(
        [latshot,lonshot],
        radius=5,
        popup=boro,
        color='crimson',
        fill=False).add_to(map_nys)


map_nys

In [41]:
## using DBSCN to visualize crime
from sklearn.cluster import DBSCAN
import sklearn.utils
from sklearn.preprocessing import StandardScaler
sklearn.utils.check_random_state(1000)
Clus_dataSet = shots_data[['Latitude','Longitude']]
Clus_dataSet = np.nan_to_num(Clus_dataSet)
Clus_dataSet = StandardScaler().fit_transform(Clus_dataSet)

In [91]:
# Compute DBSCAN #eps=.1, min =750,|||eps=.075, min_samples=200
# best cluster: db = DBSCAN(eps=.075, min_samples=150).fit(Clus_dataSet), We will DBSCAN twice to get manhattan clusters
db = DBSCAN(eps=.25, min_samples=25).fit(Clus_dataSet)
core_samples_mask = np.zeros_like(db.labels_, dtype=bool)
core_samples_mask[db.core_sample_indices_] = True
labels = db.labels_
shotsloc["Clus_Db"]=labels

realClusterNum=len(set(labels)) - (1 if -1 in labels else 0)
clusterNum = len(set(labels)) 

/home/mike/miniconda3/envs/Capstone/lib/python3.7/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


In [92]:
# A sample of clusters


In [93]:
#conda install -c conda-forge basemap
shotsloc.Clus_Db.unique()

array([-1,  0,  1,  2])

In [94]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(-1,4)
ys = [i + x + (i*x)**2 for i in range(5)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, cluster in zip(shotsloc['Latitude'], shotsloc['Longitude'], shotsloc['Clus_Db']):
    label = folium.Popup(str(' Cluster ' + str(cluster)))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
    map_clusters

# we will use folium and loop though in order to keep resolution



/home/mike/miniconda3/envs/Capstone/lib/python3.7/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [96]:
#plt.scatter(arrestloc.Latitude, arrestloc.Longitude)


Latitude  Longitude
0       40.680570 -73.983925
1       40.693587 -73.902781
2       40.675770 -73.915162
4       40.703249 -73.944275
6       40.756642 -73.988372
...           ...        ...
113639  40.763320 -73.973718
113642  40.704520 -73.893470
113645  40.678652 -73.816412
113647  40.861933 -73.893562
113648  40.823387 -73.870170

[45881 rows x 2 columns]